### Notebook to parse text files to produce cleaned text of RAD decisions

Sean Rehaag

License: Creative Commons Attribution-NonCommercial 4.0 International (CC BY-NC 4.0). 

Dataset & Code to be cited as:

Sean Rehaag, "Refugee Appeal Division Bulk Decisions Dataset" (2023), online: Refugee Law Laboratory <https://refugeelab.ca/bulk-data/rad/>.

Notes:

(1) Data Source: Immigration and Refugee Board. In the Fall of 2022, the IRB added the Refugee Law Laboratory to their email distribution list for legal publishers of RAD decisions. The RLL therefore receives new RAD cases as they are released for publication by the IRB. Also, in the fall of 2022 the Immigration and Refugee Board provided the RLL with a full backlog of approximately 116k published decisions from all divisions (RAD, RPD, ID, IAD). 

(2) Unofficial Data: The data are unofficial reproductions. For official versions, please contact the Immigration and Refugee Board. 

(3) Non-Affiliation / Endorsement: The data has been collected and reproduced without any affiliation or endorsement from the Immigration and Refugee Board.

(4) Non-Commerical Use: As indicated in the license, data may be used for non-commercial use (with attribution) only. For commercial use, please contact the Immigration and Refugee Board. 

(5) Accuracy: Data was collected and processed programmatically for the purposes of academic research. While we make best efforts to ensure accuracy, data gathering of this kind inevitably involves errors. As such the data should be viewed as preliminary information aimed to prompt further research and discussion, rather than as definitive information.

Acknowledgements: Thanks to Rafael Dolores for coding the parsing scripts.


# Installing Libraries

In [1]:
!pip install langdetect
!pip install regex

# Importing Libraries

In [2]:
import os
import regex as re 
import pandas as pd
from datetime import datetime
from langdetect import detect
from difflib import get_close_matches
import json

## Declaring Constant
Here, we specify the directories containing our data files.

In [3]:
DATA_DIRS = ["../RAD Decisions TEXT", "../IRB Decisions - Initial Request - TEXT"]

## Language Detection
This function determines the language of a given text.

In [4]:
def detect_language(text):
    try:
        return detect(text)
    except:
        return None

## Decision Maker Extraction
This function searches the given file for the decision maker using regular expressions.

In [5]:
def extract_decision_maker(content):
    patterns = [
        # String in line immediately after 'Panel' and before 'Tribunal', allowing tabs and spaces
        r"^Panel\s*([^\n]+?)\s*\n\s*Tribunal\s*$",  
      
        # String in line immediately after 'Tribunal' and before 'Panel', allowing tabs and spaces
        r"^Tribunal\s*([^\n]+?)\s*\n\s*Panel\s*$",
        # String in line immediately after 'Tribunal' and followed by another 'Tribunal', allowing tabs and spaces
        r"^Tribunal\s*([^\n]+?)\s*\n\s*Tribunal\s*$"
    ]

    for pattern in patterns:
        # Use re.MULTILINE to allow ^ and $ to match the start and end of each line
        match = re.search(pattern, content, re.IGNORECASE | re.MULTILINE)
        if match:
            captured = match.group(1).strip()
            # Check if captured group ends with 'Tribunal' or 'Panel' and exclude it
            if not captured.endswith("Tribunal") and not captured.endswith("Panel"):
                return captured
    return None



## Regular Expression Detector
Functions to parse the date from text files while accounting for several different formats

In [6]:
def match_date_patterns(content):
    patterns = {
        "custom": (r"Date (?:of decision|de la décision)\s*\n\s*([A-Za-z]+)\s+(\d{1,2})\.\s*(\d{4})", lambda m: [m.group(1), m.group(2), m.group(3)]),
        "primary": (r"Date (?:of decision|de la décision)\s*(?:Le )?\s*((?:(?:\d{1,2}|1er)\s+[\w]+\s*,?\s*\d{1,4})|\w+\s+\d{1,2}(?:st|nd|rd|th)?\s*,?\s*\d{1,4}|\d{1,2}-\d{1,2}-\d{1,4})", lambda m: m.group(1).replace(',', '').split()),
        "original_decision": (r"Date of decision\s+([\w\s]+),\s+(\d{4})\s+\(original decision\)", lambda m: m.group(1).strip().split() + [m.group(2).strip()]),
        "tribunal": (r"Tribunal\s*\n\s*([\w\s]+?)\s*\n\s*Date of decision", lambda m: m.group(1).replace(',', '').split()),
        "original": (r"Original\s+([\w]+\s+\d{1,2}(?:st|nd|rd|th)?,?\s+\d{4})", lambda m: m.group(1).replace(',', '').split())
    }

    for key, (pattern, process) in patterns.items():
        match = re.search(pattern, content, re.IGNORECASE)
        if match:
            return process(match)

    return None

## Date Formatter
Takes detected regular expression and converts into one common format

In [7]:
french_to_english = {
        'janvier': 'January', 'fevrier': 'February', 'mars': 'March', 'avril': 'April',
        'mai': 'May', 'juin': 'June', 'juillet': 'July', 'aout': 'August',
        'septembre': 'September', 'octobre': 'October', 'novembre': 'November', 'decembre': 'December'
}

def correct_month_name(misspelled_month, possibilities=['Janvier','January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December'], cutoff=0.6):
    correct_months = get_close_matches(misspelled_month, possibilities, n=1, cutoff=cutoff)
    if correct_months:
        corrected_month = correct_months[0]
        # Check if the corrected month is in the French to English mapping
        return french_to_english.get(corrected_month.lower(), corrected_month)
    else:
        return misspelled_month

def correct_year_typo(year):
    if len(year) == 3 and year.startswith("0"):
        return "20" + year[1:]
    return year

def correct_year_typo(year):
    """Corrects year format typos."""
    return "20" + year[1:] if len(year) == 3 and year.startswith("0") else year

def process_numeric_format(parts):
    """Processes numeric date format 'dd-mm-yyyy'."""
    day, month, year = parts[0].split('-')
    year = correct_year_typo(year)
    return datetime(int(year), int(month), int(day)).date().strftime('%Y-%m-%d')

def process_day_first_format(parts, french_month_mapping):
    """Processes dates in 'day month year' format, French or English."""
    day = 1 if parts[0].lower() == '1er' else int(parts[0])

    month = ''
    # Check if month and year are concatenated
    if len(parts) == 2 and not parts[1].isdigit():
        month_year_str = parts[1]
        for i in range(1, len(month_year_str)):
            if month_year_str[i:].isdigit():
                month_str, year_str = month_year_str[:i], month_year_str[i:]
                year = correct_year_typo(year_str)
                month = french_month_mapping.get(month_str.lower().replace('é', 'e').replace('û', 'u').replace('ô', 'o'), month_str.capitalize())
                break
    else:
        month = parts[1].lower().replace('é', 'e').replace('û', 'u').replace('ô', 'o')
        year = correct_year_typo(parts[2])

    if month in french_month_mapping:
        return datetime(int(year), french_month_mapping[month], day).date().strftime('%Y-%m-%d')
    else:
        if isinstance(month, int):
            return datetime(int(year), month, day).date().strftime('%Y-%m-%d')
        
        corrected_month = correct_month_name(month.capitalize())
        try:
            return datetime.strptime(f"{corrected_month} {day} {year}", '%B %d %Y').date().strftime('%Y-%m-%d')
        except ValueError as e:
            print(f"Error parsing date: {e}")
            return None

def process_month_first_format(parts):
    """Processes month first format with possible ordinal suffix."""
    day = 0
    month = ''
    year = ''
    
    if len(parts) == 2 and parts[1].isdigit() and len(parts[1]) > 2:
        
        if parts[1].isdigit() and len(parts[1]) > 4: 
            month = parts[0]
            year_str = parts[1][-4:]
            day_str = parts[1][:-4]
            year = year_str
            day = int(day_str)
            
        elif parts[1].isdigit()and len(parts[1]) > 3: #Year is the second entry
            month_day_str = parts[0]
            for i in range(1, len(month_day_str)):
                if not month_day_str[i].isdigit():
                    day_str, month_str = month_day_str[:i], month_day_str[i:]
                    day = int(day_str)
                    month = french_to_english.get(month_str.lower().replace('é', 'e').replace('û', 'u').replace('ô', 'o'), month_str)
                    parts[0] = month
                    break
            year = parts[1]
        else:
            year_str = parts[1][-4:]
            day_str = parts[1][:-4]
            year = correct_year_typo(year_str)
            day = int(day_str)

    else:
        day = re.sub(r"[^\d]", "", parts[1])
        day = int(day) if day.isdigit() else 1
        year = correct_year_typo(parts[2])
        
    
    try:
        corrected_month = correct_month_name(parts[0].capitalize())
        return datetime.strptime(f"{corrected_month} {day} {year}", '%B %d %Y').date().strftime('%Y-%m-%d')
    except ValueError as e:
        print(f"Error parsing date: {e}")
        return None


## Document Date Extraction
This function searches the given file for the document date using regular expressions, taking into account both French and English texts.

In [8]:
def process_date_parts(parts, french_month_mapping):
    """Determines the correct date processing method based on the format of the parts."""
    if '-' in parts[0]:
        return process_numeric_format(parts)
    elif parts[0].isdigit() or parts[0].lower() == '1er':
        return process_day_first_format(parts, french_month_mapping)
    else:
        return process_month_first_format(parts)

def extract_document_date(content):
    french_month_mapping = {
        'janvier': 1, 'fevrier': 2, 'mars': 3, 'avril': 4,
        'mai': 5, 'juin': 6, 'juillet': 7, 'aout': 8,
        'septembre': 9, 'octobre': 10, 'novembre': 11, 'decembre': 12
    }
    
    parts = match_date_patterns(content)
    if not parts:
        return None
    return process_date_parts(parts, french_month_mapping)

## File Processor Helpers

In [9]:
def extract_rad_number(content):
    """Extracts the RAD number from the content, ignoring IAD files."""
    # Check for lines indicating the file should be ignored
    ignore_lines = ["IAD File", "IMMIGRATION APPEAL DIVISION", "RPD File"]
    for line in content.splitlines():
        if any(ignore_line in line for ignore_line in ignore_lines):
            return None

        if "RAD File" in line:
            rad_number_match = re.search(r"([A-Z]{2}\d+-\d+)", line)
            if rad_number_match:
                return rad_number_match.group(1)
    return None

def process_file(file_path):
    """Processes a single file and extracts data."""
    with open(file_path, 'r', errors='replace') as file:
        content = file.read()

    rad_number = extract_rad_number(content)
    if rad_number:
        lang = detect_language(content)
        decision_maker_name = extract_decision_maker(content)
        document_date = extract_document_date(content)
        year = int(document_date.split('-')[0]) if document_date else None

        return {
            'citation1': rad_number,
            'citation2': '',
            'dataset': 'RAD',
            'name': '',
            'source_url': os.path.basename(file_path),
            'scraped_timestamp': datetime.now().strftime('%Y-%m-%d %H:%M:%S'),
            'document_date': document_date,
            'year': year,
            'unofficial_text': '',
            'language': lang,
            'other': json.dumps({'decision-maker_name': decision_maker_name}, ensure_ascii=False),
        }
    return None

## Processing Files
This block of code reads each file in the dataset directories to extract the needed information, using the previously defined functions and form a Pandas dataframe.

In [10]:
# Main data processing loop
data_records = []

for data_dir in DATA_DIRS:
    if os.path.exists(data_dir) and os.path.isdir(data_dir):
        for file_name in os.listdir(data_dir):
            print(f"Parsing file: {file_name}")
            if not file_name.startswith('~'):
                file_path = os.path.join(data_dir, file_name)
                record = process_file(file_path)
                if record:
                    data_records.append(record)

Parsing file: AppToReopenTB8-14702a.txt
Parsing file: AppToReopenTB8-14702tf.txt
Parsing file: Decision concerning G. Bazin (finale version) (amended 5.5.2022) (003) - sanitized.txt
Parsing file: Decision G. Bazin_ francais_modifiee (003) - sanitized.txt
Parsing file: MB7-00112a.txt
Parsing file: MB7-00112tf.txt
Parsing file: MB7-03926f.txt
Parsing file: MB7-03926ta.txt
Parsing file: MB7-24221 f.txt
Parsing file: MB7-24221ta.txt
Parsing file: MB8-01089a.txt
Parsing file: MB8-01089tf.txt
Parsing file: MB8-02514f.txt
Parsing file: MB8-02514ta.txt
Parsing file: MB8-02728.txt
Parsing file: MB8-02728tf.txt
Parsing file: MB8-02935f.txt
Parsing file: MB8-02935ta.txt
Parsing file: MB8-03538a.txt
Parsing file: MB8-03538tf.txt
Parsing file: MB8-04750f.txt
Parsing file: MB8-04750ta.txt
Parsing file: MB8-06936a.txt
Parsing file: MB8-06936tf.txt
Parsing file: MB8-07131f.txt
Parsing file: MB8-07131ta.txt
Parsing file: MB8-08060f.txt
Parsing file: MB8-08060ta.txt
Parsing file: MB8-08280f.txt
Parsing 

Parsing file: MB9-11459ta.txt
Parsing file: MB9-11472a.txt
Parsing file: MB9-11472tf.txt
Parsing file: MB9-11602f.txt
Parsing file: MB9-11602ta.txt
Parsing file: MB9-11814a.txt
Parsing file: MB9-11814tf.txt
Parsing file: MB9-11934f.txt
Parsing file: MB9-11934ta.txt
Parsing file: MB9-11939f.txt
Parsing file: MB9-11939te.txt
Parsing file: MB9-11966f.txt
Parsing file: MB9-11966te.txt
Parsing file: MB9-12342f.txt
Parsing file: MB9-12342ta.txt
Parsing file: MB9-12494a.txt
Parsing file: MB9-12494tf.txt
Parsing file: MB9-12499a.txt
Parsing file: MB9-12499tf.txt
Parsing file: MB9-12504ff.txt
Parsing file: MB9-12504ta.txt
Parsing file: MB9-12537f.txt
Parsing file: MB9-12537ta.txt
Parsing file: MB9-12551a.txt
Parsing file: MB9-12551f.txt
Parsing file: MB9-12570a.txt
Parsing file: MB9-12570tf.txt
Parsing file: MB9-12573f.txt
Parsing file: MB9-12573ta.txt
Parsing file: MB9-12581f.txt
Parsing file: MB9-12581ta.txt
Parsing file: MB9-12821a.txt
Parsing file: MB9-12821tf.txt
Parsing file: MB9-12848f.t

Parsing file: MB9-21127ta.txt
Parsing file: MB9-21267f.txt
Parsing file: MB9-21267ta.txt
Parsing file: MB9-21516f.txt
Parsing file: MB9-21516ta.txt
Parsing file: MB9-21654a.txt
Parsing file: MB9-21654tf.txt
Parsing file: MB9-21655a.txt
Parsing file: MB9-21655tf.txt
Parsing file: MB9-21656a.txt
Parsing file: MB9-21656tf.txt
Parsing file: MB9-21661f.txt
Parsing file: MB9-21661ta.txt
Parsing file: MB9-21802a.txt
Parsing file: MB9-21802tf.txt
Parsing file: MB9-21924f.txt
Parsing file: MB9-21924ta.txt
Parsing file: MB9-21926 a.txt
Parsing file: MB9-21926tf.txt
Parsing file: MB9-21935f.txt
Parsing file: MB9-21935ta.txt
Parsing file: MB9-21941f.txt
Parsing file: MB9-21941ta.txt
Parsing file: MB9-22048a.txt
Parsing file: MB9-22048tf.txt
Parsing file: MB9-22375a.txt
Parsing file: MB9-22375tf.txt
Parsing file: MB9-22411a.txt
Parsing file: MB9-22411tf.txt
Parsing file: MB9-22713f.txt
Parsing file: MB9-22713ta.txt
Parsing file: MB9-22724f.txt
Parsing file: MB9-22724ta.txt
Parsing file: MB9-22726a.

Parsing file: MC0-01687tf.txt
Parsing file: MC0-01705a.txt
Parsing file: MC0-01705tf.txt
Parsing file: MC0-01793 f.txt
Parsing file: MC0-01793ta.txt
Parsing file: MC0-01794 a.txt
Parsing file: MC0-01794tf.txt
Parsing file: MC0-01798a.txt
Parsing file: MC0-01798tf.txt
Parsing file: MC0-01801 a.txt
Parsing file: MC0-01801tf.txt
Parsing file: MC0-01907f.txt
Parsing file: MC0-01907ta.txt
Parsing file: MC0-01913f.txt
Parsing file: MC0-01913ta.txt
Parsing file: MC0-01917 a.txt
Parsing file: MC0-01917tf.txt
Parsing file: MC0-01918f.txt
Parsing file: MC0-01918ta.txt
Parsing file: MC0-02034f .txt
Parsing file: MC0-02034ta.txt
Parsing file: MC0-02054f.txt
Parsing file: MC0-02054ta.txt
Parsing file: MC0-02055a.txt
Parsing file: MC0-02055tf.txt
Parsing file: MC0-02058f.txt
Parsing file: MC0-02058ta.txt
Parsing file: MC0-02182f .txt
Parsing file: MC0-02182ta.txt
Parsing file: MC0-02183f .txt
Parsing file: MC0-02183ta.txt
Parsing file: MC0-02199f.txt
Parsing file: MC0-02199ta.txt
Parsing file: MC0-0

Parsing file: MC0-08828a.txt
Parsing file: MC0-08828tf.txt
Parsing file: MC0-08834 a.txt
Parsing file: MC0-08834tf.txt
Parsing file: MC0-08857 a.txt
Parsing file: MC0-08857tf.txt
Parsing file: MC0-08908 a.txt
Parsing file: MC0-08908tf.txt
Parsing file: MC0-08913 f.txt
Parsing file: MC0-08913ta.txt
Parsing file: MC0-08939 a.txt
Parsing file: MC0-08939tf.txt
Parsing file: MC0-08954a.txt
Parsing file: MC0-08954tf.txt
Parsing file: MC0-08972a.txt
Parsing file: MC0-08972tf.txt
Parsing file: MC0-08998 a.txt
Parsing file: MC0-08998tf.txt
Parsing file: MC0-09001a.txt
Parsing file: MC0-09001tf.txt
Parsing file: MC0-09023a.txt
Parsing file: MC0-09023tf.txt
Parsing file: MC0-09027 a.txt
Parsing file: MC0-09027tf.txt
Parsing file: MC0-09038 f.txt
Parsing file: MC0-09038ta.txt
Parsing file: MC0-09063 a.txt
Parsing file: MC0-09063tf.txt
Parsing file: MC0-09072a.txt
Parsing file: MC0-09072tf.txt
Parsing file: MC0-09130a.txt
Parsing file: MC0-09130tf.txt
Parsing file: MC0-09170f.txt
Parsing file: MC0-

...

Parsing file: 923744.txt
Parsing file: 923749.txt
Parsing file: 923754.txt
Parsing file: 923764.txt
Parsing file: 923765.txt
Parsing file: 923766.txt
Parsing file: 923770.txt
Parsing file: 923771.txt
Parsing file: 923772.txt
Parsing file: 923773.txt
Parsing file: 923774.txt
Parsing file: 923778.txt
Parsing file: 923779.txt
Parsing file: 923783.txt
Parsing file: 923789.txt
Parsing file: 923797.txt
Parsing file: 923798.txt
Parsing file: 923800.txt
Parsing file: 923839.txt
Parsing file: 923840.txt
Parsing file: 923843.txt
Parsing file: 923844.txt
Parsing file: 923847.txt
Parsing file: 923849.txt
Parsing file: 923851.txt
Parsing file: 923852.txt
Parsing file: 923856.txt
Parsing file: 923857.txt
Parsing file: 923858.txt
Parsing file: 923860.txt
Parsing file: 923862.txt
Parsing file: 923863.txt
Parsing file: 923864.txt
Parsing file: 923865.txt
Parsing file: 923866.txt
Parsing file: 923868.txt
Parsing file: 923869.txt
Parsing file: 923870.txt
Parsing file: 923873.txt
Parsing file: 923875.txt


Parsing file: 954736.txt
Parsing file: 955515.txt
Parsing file: 955516.txt
Parsing file: 955518.txt
Parsing file: 955519.txt
Parsing file: 955520.txt
Parsing file: 955522.txt
Parsing file: 955523.txt
Parsing file: 955524.txt
Parsing file: 955526.txt
Parsing file: 955530.txt
Parsing file: 955531.txt
Parsing file: 955532.txt
Parsing file: 955534.txt
Parsing file: 955535.txt
Parsing file: 955536.txt
Parsing file: 955537.txt
Parsing file: 955539.txt
Parsing file: 955540.txt
Parsing file: 955542.txt
Parsing file: 955543.txt
Parsing file: 955544.txt
Parsing file: 955545.txt
Parsing file: 955546.txt
Parsing file: 955547.txt
Parsing file: 955548.txt
Parsing file: 955550.txt
Parsing file: 955551.txt
Parsing file: 955552.txt
Parsing file: 955553.txt
Parsing file: 955843.txt
Parsing file: 955844.txt
Parsing file: 955845.txt
Parsing file: 955847.txt
Parsing file: 955849.txt
Parsing file: 955850.txt
Parsing file: 955852.txt
Parsing file: 955853.txt
Parsing file: 955856.txt
Parsing file: 955857.txt


Parsing file: 970598.txt
Parsing file: 970601.txt
Parsing file: 970602.txt
Parsing file: 970605.txt
Parsing file: 970608.txt
Parsing file: 970609.txt
Parsing file: 970611.txt
Parsing file: 970612.txt
Parsing file: 970616.txt
Parsing file: 970618.txt
Parsing file: 970622.txt
Parsing file: 970623.txt
Parsing file: 970628.txt
Parsing file: 970630.txt
Parsing file: 970631.txt
Parsing file: 970632.txt
Parsing file: 970633.txt
Parsing file: 970634.txt
Parsing file: 970638.txt
Parsing file: 970639.txt
Parsing file: 970640.txt
Parsing file: 970983.txt
Parsing file: 970987.txt
Parsing file: 970992.txt
Parsing file: 971007.txt
Parsing file: 971009.txt
Parsing file: 971018.txt
Parsing file: 971030.txt
Parsing file: 971042.txt
Parsing file: 971046.txt
Parsing file: 971050.txt
Parsing file: 971051.txt
Parsing file: 971052.txt
Parsing file: 971059.txt
Parsing file: 971065.txt
Parsing file: 971067.txt
Parsing file: 971069.txt
Parsing file: 971071.txt
Parsing file: 971072.txt
Parsing file: 971073.txt


Parsing file: 983120.txt
Parsing file: 983122.txt
Parsing file: 983123.txt
Parsing file: 983124.txt
Parsing file: 983125.txt
Parsing file: 983126.txt
Parsing file: 983127.txt
Parsing file: 983129.txt
Parsing file: 983133.txt
Parsing file: 983134.txt
Parsing file: 983135.txt
Parsing file: 983140.txt
Parsing file: 983141.txt
Parsing file: 983142.txt
Parsing file: 983143.txt
Parsing file: 983144.txt
Parsing file: 983145.txt
Parsing file: 983146.txt
Parsing file: 983147.txt
Parsing file: 983148.txt
Parsing file: 983150.txt
Parsing file: 983151.txt
Parsing file: 983153.txt
Parsing file: 983154.txt
Parsing file: 983155.txt
Parsing file: 983156.txt
Parsing file: 985217.txt
Parsing file: 985231.txt
Parsing file: 987012.txt
Parsing file: 987019.txt
Parsing file: 988646.txt
Parsing file: 988648.txt
Parsing file: 988649.txt
Parsing file: 988651.txt
Parsing file: 988652.txt
Parsing file: 988654.txt
Parsing file: 988655.txt
Parsing file: 988657.txt
Parsing file: 988658.txt
Parsing file: 988659.txt


Parsing file: 992757.txt
Parsing file: 992758.txt
Parsing file: 992759.txt
Parsing file: 992762.txt
Parsing file: 992763.txt
Parsing file: 992764.txt
Parsing file: 992765.txt
Parsing file: 992766.txt
Parsing file: 992767.txt
Parsing file: 992768.txt
Parsing file: 992769.txt
Parsing file: 992771.txt
Parsing file: 992772.txt
Parsing file: 992774.txt
Parsing file: 992775.txt
Parsing file: 992776.txt
Parsing file: 992777.txt
Parsing file: 992778.txt
Parsing file: 992779.txt
Parsing file: 992780.txt
Parsing file: 992782.txt
Parsing file: 992783.txt
Parsing file: 992785.txt
Parsing file: 992787.txt
Parsing file: 992788.txt
Parsing file: 992789.txt
Parsing file: 992790.txt
Parsing file: 992793.txt
Parsing file: 992794.txt
Parsing file: 992795.txt
Parsing file: 992796.txt
Parsing file: 992797.txt
Parsing file: 992798.txt
Parsing file: 992799.txt
Parsing file: 992800.txt
Parsing file: 992803.txt
Parsing file: 992804.txt
Parsing file: 992806.txt
Parsing file: 992807.txt
Parsing file: 992809.txt


## Placing output in DATA/YEARLY format jsons
Converts dataframe into segregated jsons based on the document's year for efficient storage

In [11]:
df = pd.DataFrame(data_records)
df['document_date'] = pd.to_datetime(df['document_date']).dt.strftime('%Y-%m-%d')
output_dir = 'DATA/YEARLY'
os.makedirs(output_dir, exist_ok=True)

total_records = 0
for year, group in df.groupby('year'):
    json_path = os.path.join(output_dir, f'{int(year)}.json')
    

    records = group.to_dict(orient='records')
    
    # Write the records to a JSON file
    total_records += len(records)
    with open(json_path, 'w', encoding='utf-8') as f:
        json.dump(records, f, ensure_ascii=False, indent=4)
    
    print(f'Outputted {len(records)} records to {json_path}')

print(f'Total records: {total_records}')

Outputted 2 records to DATA/YEARLY\2010.json
Outputted 1 records to DATA/YEARLY\2011.json
Outputted 759 records to DATA/YEARLY\2013.json
Outputted 2569 records to DATA/YEARLY\2014.json
Outputted 3456 records to DATA/YEARLY\2015.json
Outputted 2227 records to DATA/YEARLY\2016.json
Outputted 1005 records to DATA/YEARLY\2017.json
Outputted 1986 records to DATA/YEARLY\2018.json
Outputted 4579 records to DATA/YEARLY\2019.json
Outputted 6298 records to DATA/YEARLY\2020.json
Outputted 3765 records to DATA/YEARLY\2021.json
Outputted 139 records to DATA/YEARLY\2022.json
Outputted 2 records to DATA/YEARLY\2023.json
Total records: 26788
